# Read Dataset

In [2]:
import sys, os
sys.path.append(os.path.split(os.getcwd())[0])
import utils
import glob

In [9]:
import re

def atoi(text):
    return int(text) if text.isdigit() else text
def natural_keys(text):
    '''
    alist.sort(key=natural_keys) sorts in human order
    http://nedbatchelder.com/blog/200712/human_sorting.html
    (See Toothy's implementation in the comments)
    '''
    return [ atoi(c) for c in re.split('(\d+)', text) ]

dataset_dir = "../dataset/"
files = glob.glob(dataset_dir+"p*.txt")
files.sort(key=natural_keys)
docs = [utils.read_file(x) for x in files]
files

['../dataset/p0.txt',
 '../dataset/p1.txt',
 '../dataset/p2.txt',
 '../dataset/p3.txt',
 '../dataset/p4.txt',
 '../dataset/p5.txt',
 '../dataset/p6.txt',
 '../dataset/p7.txt',
 '../dataset/p8.txt',
 '../dataset/p9.txt',
 '../dataset/p10.txt',
 '../dataset/p11.txt',
 '../dataset/p12.txt',
 '../dataset/p13.txt',
 '../dataset/p14.txt',
 '../dataset/p15.txt',
 '../dataset/p16.txt',
 '../dataset/p17.txt',
 '../dataset/p18.txt',
 '../dataset/p19.txt',
 '../dataset/p20.txt',
 '../dataset/p21.txt',
 '../dataset/p22.txt',
 '../dataset/p23.txt',
 '../dataset/p24.txt',
 '../dataset/p25.txt',
 '../dataset/p26.txt',
 '../dataset/p27.txt',
 '../dataset/p28.txt',
 '../dataset/p29.txt',
 '../dataset/p30.txt',
 '../dataset/p31.txt',
 '../dataset/p32.txt',
 '../dataset/p33.txt',
 '../dataset/p34.txt',
 '../dataset/p35.txt',
 '../dataset/p36.txt',
 '../dataset/p37.txt',
 '../dataset/p38.txt',
 '../dataset/p39.txt',
 '../dataset/p40.txt',
 '../dataset/p41.txt',
 '../dataset/p42.txt',
 '../dataset/p43.txt'

In [19]:
docs

[u'LOW, B RYAN K IAN H SIANG Assistant Professor, Jan 2010 - Present Department of Computer Science School of Computing, National University of Singapore Computing 1, 13 Computing Drive, Singapore 117417, Singapore Deputy Director of AI Research & Technology, Mar 2018 - Present AI Singapore Email: lowkh@comp.nus.edu.sg Web: http://www.comp.nus.edu.sg/lowkh  C URRICULUM V ITAE  R ESEARCH I NTERESTS      Probabilistic machine learning (e.g., Bayesian deep learning, Bayesian non-parametric models) Data-efficient machine learning (e.g., Bayesian optimization, active learning, and adaptive sampling) Parallel/distributed machine learning and online learning for big data Planning under uncertainty and reinforcement learning Multi-agent systems (i.e., multi-agent coordination, planning, and learning)  E DUCATIONAL BACKGROUND Sep 2004 - Aug 2009 Carnegie Mellon University P H .D. IN E LECTRICAL AND C OMPUTER E NGINEERING  Thesis Title: Multi-Robot Adaptive Exploration and Mapping for Environmen

In [10]:
import spacy
nlp = spacy.load('en')

In [11]:
%%time
processed_docs = []    
for doc in nlp.pipe(docs, n_threads=4, batch_size=100):
    # Process document using Spacy NLP pipeline.
    
    ents = doc.ents  # Named entities.

    # Keep only words (no numbers, no punctuation).
    # Lemmatize tokens, remove punctuation and remove stopwords.
    doc = [token.lemma_ for token in doc if token.is_alpha and not token.is_stop]

    # Remove common words from a stopword list.
    #doc = [token for token in doc if token not in STOPWORDS]

    # Add named entities, but only if they are a compound of more than word.
    doc.extend([str(entity) for entity in ents if len(entity) > 1])
    
    processed_docs.append(doc)
    
# This method takes roughly ~ 3 mins

CPU times: user 3min 40s, sys: 57.3 s, total: 4min 37s
Wall time: 2min 43s


In [12]:
docs = processed_docs
del processed_docs

In [13]:
# Compute bigrams.
from gensim.models import Phrases
# Add bigrams and trigrams to docs (only ones that appear 20 times or more).
bigram = Phrases(docs, min_count=20)
for idx in range(len(docs)):
    for token in bigram[docs[idx]]:
        if '_' in token:
            # Token is a bigram, add to document.
            docs[idx].append(token)

In [14]:
# Create a dictionary representation of the documents, and filter out frequent and rare words.

from gensim.corpora import Dictionary
dictionary = Dictionary(docs)

# Remove rare and common tokens.
# Filter out words that occur too frequently or too rarely.
max_freq = 0.5
min_wordcount = 20
dictionary.filter_extremes(no_below=min_wordcount, no_above=max_freq)

_ = dictionary[0]  # This sort of "initializes" dictionary.id2token.

In [15]:
# Vectorize data.

# Bag-of-words representation of the documents.
corpus = [dictionary.doc2bow(doc) for doc in docs]

In [20]:
len(corpus)

90

In [22]:
author2doc = utils.read_json_file("../dataset/authors.json")
author2doc

{u'Bryan_Low': [0,
  1,
  2,
  3,
  4,
  5,
  6,
  7,
  8,
  9,
  10,
  11,
  12,
  13,
  14,
  15,
  16,
  17,
  18,
  19,
  20,
  21],
 u'David_Hsu': [22,
  23,
  24,
  25,
  26,
  27,
  28,
  29,
  30,
  31,
  32,
  33,
  34,
  35,
  36,
  37,
  38,
  39],
 u'Harold_Soh': [83, 84, 85, 86, 87, 88, 89, 36, 37],
 u'Kuldeep_S._Meel': [50,
  51,
  52,
  53,
  54,
  55,
  56,
  57,
  58,
  59,
  60,
  61,
  62,
  63,
  64,
  65,
  66,
  67,
  68,
  69,
  70,
  71],
 u'Lee_Wee_Sun': [40,
  24,
  25,
  27,
  41,
  42,
  43,
  30,
  44,
  45,
  46,
  32,
  33,
  47,
  35,
  48,
  49,
  38,
  39],
 u'Leong_Tze_Yun': [72, 73, 74, 75, 76, 77, 78, 79, 80, 81, 82]}

In [23]:
from gensim.models import AuthorTopicModel
%time model = AuthorTopicModel(corpus=corpus, num_topics=10, id2word=dictionary.id2token, \
                author2doc=author2doc, chunksize=10, passes=1, eval_every=0, \
                iterations=1, random_state=1)

CPU times: user 34.2 ms, sys: 1.58 ms, total: 35.8 ms
Wall time: 34.4 ms


In [27]:
%%time
model_list = []
for i in range(5):
    model = AuthorTopicModel(corpus=corpus, num_topics=5, id2word=dictionary.id2token, \
                    author2doc=author2doc, chunksize=2000, passes=100, gamma_threshold=1e-10, \
                    eval_every=0, iterations=1, random_state=i)
    top_topics = model.top_topics(corpus)
    tc = sum([t[1] for t in top_topics])
    model_list.append((model, tc))

CPU times: user 9.47 s, sys: 24.2 ms, total: 9.5 s
Wall time: 9.52 s


In [28]:
model, tc = max(model_list, key=lambda x: x[1])
print('Topic coherence: %.3e' %tc)

Topic coherence: -3.736e+00


In [29]:
model.show_topics(num_topics=5)

[(0,
  u'0.026*"kernel" + 0.021*"cluster" + 0.019*"pp" + 0.019*"version" + 0.016*"object" + 0.015*"neural" + 0.013*"gaussian" + 0.010*"x_x" + 0.010*"local" + 0.010*"gp"'),
 (1,
  u'0.035*"human" + 0.028*"policy" + 0.019*"action" + 0.019*"object" + 0.015*"pomdp" + 0.012*"of" + 0.012*"belief" + 0.010*"reward" + 0.009*"and" + 0.009*"tree"'),
 (2,
  u'0.032*"action" + 0.027*"concept" + 0.024*"policy" + 0.015*"reward" + 0.014*"relation" + 0.014*"transition" + 0.012*"heuristic" + 0.012*"sampling" + 0.011*"context" + 0.010*"arm"'),
 (3,
  u'0.026*"gp" + 0.018*"gaussian" + 0.017*"agent" + 0.016*"q" + 0.011*"predictive" + 0.011*"z" + 0.010*"gaussian_process" + 0.010*"active" + 0.010*"local" + 0.010*"sparse"'),
 (4,
  u'0.027*"formula" + 0.021*"count" + 0.019*"counting" + 0.019*"q" + 0.017*"benchmark" + 0.014*"witness" + 0.012*"lemma" + 0.012*"pr" + 0.011*"counter" + 0.011*"solver"')]

In [40]:
topic_labels = ['Gaussian Kernels', 'POMPD', 'Reinforcement Learning', 'Gaussian Process', \
               'Sampling & Counting']

In [42]:
for topic in model.show_topics(num_topics=5):
    print('Label: ' + topic_labels[topic[0]])
    words = ''
    for word, prob in model.show_topic(topic[0]):
        words += word + ' '
    print('Words: ' + words)
    print()

Label: Gaussian Kernels
Words: kernel cluster pp version object neural gaussian x_x local gp 
()
Label: POMPD
Words: human policy action object pomdp of belief reward and tree 
()
Label: Reinforcement Learning
Words: action concept policy reward relation transition heuristic sampling context arm 
()
Label: Gaussian Process
Words: gp gaussian agent q predictive z gaussian_process active local sparse 
()
Label: Sampling & Counting
Words: formula count counting q benchmark witness lemma pr counter solver 
()


In [33]:
model['Leong_Tze_Yun']

[(2, 0.9998921851934642)]

In [34]:
from pprint import pprint

def show_author(name):
    print('\n%s' % name)
    print('Docs:', model.author2doc[name])
    print('Topics:')
    pprint([(topic_labels[topic[0]], topic[1]) for topic in model[name]])

In [41]:
for author in author2doc.keys():
    show_author(author)


David_Hsu
('Docs:', [22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39])
Topics:
[('POMPD', 0.9959444126054385)]

Bryan_Low
('Docs:', [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21])
Topics:
[('Gaussian Process', 0.9999690668406681)]

Leong_Tze_Yun
('Docs:', [72, 73, 74, 75, 76, 77, 78, 79, 80, 81, 82])
Topics:
[('Reinforcement Learning', 0.9998921851934642)]

Harold_Soh
('Docs:', [83, 84, 85, 86, 87, 88, 89, 36, 37])
Topics:
[('Gaussian Kernels', 0.9979838251162345)]

Kuldeep_S._Meel
('Docs:', [50, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 62, 63, 64, 65, 66, 67, 68, 69, 70, 71])
Topics:
[('Sampling & Counting', 0.9999757439851281)]

Lee_Wee_Sun
('Docs:', [40, 24, 25, 27, 41, 42, 43, 30, 44, 45, 46, 32, 33, 47, 35, 48, 49, 38, 39])
Topics:
[('Gaussian Kernels', 0.06127650026748347), ('POMPD', 0.9386861018060448)]
